# Thiết lập

In [1]:
!pip install openai

import time
import numpy as np
import json
import openai
import random
import argparse
from google.colab import files

# Tải tệp JSON nếu cần thiết
uploaded = files.upload()

# Xử lý đối số argparse
parser = argparse.ArgumentParser()

parser.add_argument('--length_limit', type=int, default=8, help='')
parser.add_argument('--num_cand', type=int, default=19, help='')
parser.add_argument('--random_seed', type=int, default=2023, help='')
parser.add_argument('--api_key', type=str, default="sk-", help="")

# Thêm dòng này để cung cấp các đối số cho parse_args()
args = parser.parse_args(args=[])

rseed = args.random_seed
random.seed(rseed)

def read_json(file):
    with open(file) as f:
        return json.load(f)

def write_json(data, file):
    with open(file, 'w', encoding='utf-8') as f:
        json.dump(data, f, ensure_ascii=False, indent=2)

# Đọc tệp JSON từ các tệp đã tải lên
data_ml_100k = read_json("ml_100k.json")

print (data_ml_100k[0][0])
print (data_ml_100k[0][1])
print (len(data_ml_100k))


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 375.0/375.0 kB 6.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.4/76.4 kB 3.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 77.9/77.9 kB 2.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 318.9/318.9 kB 8.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 2.8 MB/s eta 0:00:00


Saving ml_100k.json to ml_100k.json
My Best Friend's Wedding | The English Patient | Face/Off | Psycho | The Princess Bride | Kids | Kids in the Hall: Brain Candy | Scream | The Craft | The Rock | The Shining | Mission: Impossible | Reality Bites | Aliens | Indiana Jones and the Last Crusade | One Flew Over the Cuckoo's Nest | In the Name of the Father | Return of the Jedi | The Silence of the Lambs | The Usual Suspects | Dances with Wolves | Monty Python's Life of Brian | Monty Python and the Holy Grail | The Full Monty | Clockwork Orange, A | Apocalypse Now | Trainspotting | The Doors | Mr. Holland's Opus | Independence Day (ID4) | Liar Liar | Titanic | What's Eating Gilbert Grape | The Saint | Donnie Brasco | The Empire Strikes Back | Beautiful Girls | Mars Attacks! | Broken Arrow | Amistad | The Long Kiss Goodnight | French Kiss | The Maltese Falcon | Dazed and Confused | Strange Days
Starship Troopers
943


In [2]:
u_item_dict = {}                                                     # Khởi tạo một từ điển rỗng để lưu trữ ánh xạ từ tên phim đến chỉ số duy nhất.
u_item_p = 0                                                         # Khởi tạo biến đếm để gán chỉ số cho từng phim.
for elem in data_ml_100k:
    seq_list = elem[0].split(' | ')                                  # Tách chuỗi phim trong phần tử hiện tại thành danh sách các phim, sử dụng ký tự ' | ' làm dấu phân cách.
    for movie in seq_list:
        if movie not in u_item_dict:
            u_item_dict[movie] = u_item_p                            # Nếu phim chưa có trong từ điển, thêm nó vào từ điển với chỉ số hiện tại
            u_item_p +=1                                             # Tăng biến đếm u_item_p lên 1 để chuẩn bị cho phim tiếp theo.
print (len(u_item_dict))                                             # In ra số lượng phim duy nhất đã được thêm vào từ điển.
u_item_len = len(u_item_dict)                                        # Lưu trữ độ dài của từ điển u_item_dict vào biến u_item_len

1493


Đoạn mã này tạo ra một từ điển ánh xạ các phim từ dữ liệu data_ml_100k thành các chỉ số duy nhất. Mỗi phim chỉ xuất hiện một lần trong từ điển với một chỉ số duy nhất, và biến u_item_p được sử dụng để gán chỉ số này. Cuối cùng, đoạn mã in ra số lượng phim duy nhất và lưu trữ độ dài của từ điển.

In [6]:
user_list = []                                                       # Khởi tạo một danh sách rỗng để lưu trữ danh sách các phim của từng người dùng.
for i, elem in  enumerate(data_ml_100k):
    item_hot_list = [0 for ii in range(u_item_len)]                  # Tạo một danh sách với độ dài bằng số lượng phim (u_item_len), tất cả các giá trị ban đầu là 0. Danh sách này sẽ được sử dụng để đánh dấu các phim mà người dùng đã xem.
    seq_list = elem[0].split(' | ')
    for movie in seq_list:
        item_pos = u_item_dict[movie]                                # Lấy chỉ số tương ứng của phim trong từ điển u_item_dict.
        item_hot_list[item_pos] = 1                                  # Đánh dấu phim này là đã xem (giá trị 1) trong danh sách item_hot_list
    user_list.append(item_hot_list)                                  # Thêm danh sách item_hot_list vào danh sách người dùng user_list.
user_matrix = np.array(user_list)                                    # Chuyển đổi danh sách người dùng user_list thành ma trận numpy user_matrix.
user_matrix_sim = np.dot(user_matrix, user_matrix.transpose())       # Tính toán ma trận tương đồng giữa các người dùng bằng cách nhân ma trận user_matrix với ma trận chuyển vị của nó (user_matrix.transpose())
                                                                     # Kết quả là một ma trận mà mỗi phần tử (i, j) đại diện cho độ tương đồng giữa người dùng i và người dùng j.

Đoạn mã này tạo ra một ma trận người dùng từ dữ liệu data_ml_100k, trong đó mỗi hàng đại diện cho một người dùng và mỗi cột đại diện cho một phim. Giá trị 1 trong ma trận biểu thị rằng người dùng đã xem phim đó, trong khi giá trị 0 biểu thị rằng người dùng chưa xem phim đó. Sau đó, đoạn mã tính toán ma trận tương đồng giữa các người dùng, giúp xác định mức độ tương đồng giữa các người dùng dựa trên các phim mà họ đã xem.

In [5]:
pop_dict = {}                          # Khởi tạo một từ điển rỗng để lưu trữ độ phổ biến của các phim. Mỗi phim sẽ là một khóa trong từ điển, và giá trị tương ứng sẽ là số lần phim đó xuất hiện trong dữ liệu.
for elem in data_ml_100k:
    elem = data_ml_100k[i]
    seq_list = elem[0].split(' | ')    # Tách chuỗi phim trong phần tử hiện tại thành danh sách các phim,
    for movie in seq_list:
        if movie not in pop_dict:
              pop_dict[movie] = 0      # Nếu phim chưa có trong từ điển, thêm nó vào từ điển với giá trị ban đầu là 0.
        pop_dict[movie] += 1           # Tăng giá trị đếm của phim lên 1, biểu thị rằng phim này đã xuất hiện thêm một lần trong dữ liệu.

Đoạn mã này tạo ra một từ điển pop_dict để lưu trữ độ phổ biến của các phim trong dữ liệu data_ml_100k. Mỗi phim sẽ là một khóa trong từ điển, và giá trị tương ứng sẽ là số lần phim đó xuất hiện trong dữ liệu. Vòng lặp duyệt qua từng phần tử trong dữ liệu, tách chuỗi phim thành danh sách, và cập nhật từ điển pop_dict với số lần xuất hiện của từng phim.

In [4]:
i_item_dict = {}                 # Khởi tạo từ điển rỗng để ánh xạ tên phim thành chỉ số duy nhất
i_item_id_list = []              # Khởi tạo danh sách rỗng để lưu trữ tên các phim theo thứ tự chỉ số
i_item_user_dict = {}            # Khởi tạo từ điển rỗng để lưu trữ danh sách người dùng đã xem mỗi phim
i_item_p = 0                     # Khởi tạo biến đếm để gán chỉ số cho từng phim

for i, elem in enumerate(data_ml_100k):
    seq_list = elem[0].split(' | ')
    for movie in seq_list:
        if movie not in i_item_user_dict:                            # Nếu phim chưa có trong từ điển i_item_user_dict
            item_hot_list = [0. for ii in range(len(data_ml_100k))]  # Tạo danh sách với độ dài bằng số lượng người dùng, tất cả các giá trị ban đầu là 0
            i_item_user_dict[movie] = item_hot_list                  # Thêm phim vào từ điển i_item_user_dict với danh sách người dùng đã xem phim đó
            i_item_dict[movie] = i_item_p                            # Thêm phim vào từ điển i_item_dict với chỉ số hiện tại i_item_p
            i_item_id_list.append(movie)                             # Thêm phim vào danh sách i_item_id_list
            i_item_p += 1                                            # Tăng biến đếm i_item_p lên 1 để chuẩn bị cho phim tiếp theo

        item_pos = i_item_dict[movie]                # Lấy chỉ số của phim từ từ điển i_item_dict
        i_item_user_dict[movie][i] += 1              # Đánh dấu rằng người dùng i đã xem phim này
    user_list.append(item_hot_list)                  # Thêm danh sách item_hot_list vào danh sách người dùng user_list

i_item_s_list = []               # Khởi tạo danh sách rỗng để lưu trữ danh sách người dùng đã xem mỗi phim
for item in i_item_id_list:
    i_item_s_list.append(i_item_user_dict[item])     # Thêm danh sách người dùng đã xem phim vào i_item_s_list
    print(sum(i_item_user_dict[item]))               # Kiểm tra tổng số lần xuất hiện của phim trong dữ liệu

item_matrix = np.array(i_item_s_list)                           # Chuyển đổi danh sách i_item_s_list thành ma trận numpy item_matrix
item_matrix_sim = np.dot(item_matrix, item_matrix.transpose())  # Tính toán ma trận tương đồng giữa các phim

id_list = list(range(0, len(data_ml_100k)))                     # Tạo danh sách các chỉ số người dùng từ 0 đến len(data_ml_100k) - 1

100.0
240.0
79.0
81.0
107.0
16.0
29.0
225.0
43.0
154.0
80.0
143.0
46.0
93.0
115.0
84.0
33.0
191.0
131.0
85.0
79.0
44.0
101.0
176.0
77.0
62.0
89.0
17.0
136.0
196.0
229.0
209.0
27.0
160.0
62.0
117.0
42.0
84.0
119.0
78.0
84.0
38.0
50.0
25.0
21.0
1.0
77.0
59.0
163.0
40.0
38.0
34.0
37.0
17.0
4.0
161.0
33.0
34.0
31.0
32.0
129.0
44.0
11.0
15.0
6.0
8.0
92.0
92.0
24.0
65.0
4.0
137.0
9.0
23.0
11.0
91.0
13.0
7.0
121.0
60.0
252.0
85.0
84.0
73.0
88.0
54.0
166.0
102.0
98.0
52.0
8.0
40.0
14.0
74.0
30.0
48.0
11.0
40.0
4.0
28.0
12.0
45.0
25.0
18.0
14.0
20.0
13.0
77.0
31.0
15.0
34.0
39.0
29.0
31.0
17.0
8.0
29.0
60.0
38.0
32.0
45.0
31.0
27.0
14.0
45.0
7.0
13.0
7.0
11.0
12.0
17.0
19.0
16.0
24.0
23.0
18.0
30.0
76.0
51.0
5.0
29.0
19.0
77.0
12.0
1.0
121.0
62.0
54.0
20.0
16.0
74.0
26.0
24.0
22.0
61.0
4.0
86.0
54.0
107.0
40.0
22.0
51.0
234.0
20.0
68.0
60.0
59.0
14.0
9.0
5.0
22.0
47.0
69.0
4.0
129.0
11.0
33.0
68.0
15.0
10.0
5.0
49.0
40.0
56.0
15.0
28.0
34.0
24.0
18.0
101.0
146.0
16.0
106.0
50.0
93.0
61.0
33.0
1

Đoạn mã này tạo ra các cấu trúc dữ liệu để lưu trữ thông tin về các phim và người dùng, sau đó tính toán ma trận tương đồng giữa các phim. Mỗi phim được ánh xạ đến một chỉ số duy nhất và danh sách người dùng đã xem phim đó được lưu trữ. Cuối cùng, đoạn mã tính toán ma trận tương đồng giữa các phim, giúp xác định mức độ tương đồng giữa các phim dựa trên người dùng đã xem chúng.

# User filtering

In [13]:
def sort_uf_items(target_seq, us, num_u, num_i, data_ml_100k):
    candidate_movies_dict = {}  # Dictionary để lưu các phim ứng viên

    # Sắp xếp danh sách người dùng dựa trên điểm số `us` và lấy ra `num_u` người dùng hàng đầu
    sorted_us = sorted(list(enumerate(us)), key=lambda x: x[-1], reverse=True)[:num_u]

    # Tính tổng điểm của các người dùng được chọn
    dvd = sum([e[-1] for e in sorted_us])

    for us_i, us_v in sorted_us:
        us_w = us_v * 1.0 / dvd  # Tính trọng số của mỗi người dùng dựa trên tỷ lệ điểm
        print(f"User index: {us_i}")

        # Lấy chuỗi tương ứng của người dùng từ `data_ml_100k`
        us_elem = data_ml_100k[us_i]
        print(f"User element (first): {us_elem[0]}")

        # Tách danh sách phim mà người dùng này đã xem
        us_seq_list = us_elem[0].split(' | ')

        for us_m in us_seq_list:
            print(f"{us_m} not in {target_seq}, {us_m not in target_seq}")

            # Chỉ thêm các phim mà không nằm trong `target_seq`
            if us_m not in target_seq:
                if us_m not in candidate_movies_dict:
                    candidate_movies_dict[us_m] = 0.0  # Nếu phim chưa có trong dictionary, khởi tạo giá trị 0
                candidate_movies_dict[us_m] += us_w  # Cộng trọng số của người dùng vào phim này

    # Sắp xếp danh sách phim ứng viên theo điểm số giảm dần
    candidate_pairs = sorted(candidate_movies_dict.items(), key=lambda x: x[-1], reverse=True)
    print("Sorted candidate pairs:", candidate_pairs)

    # Lấy ra `num_i` phim có điểm số cao nhất
    candidate_items = [e[0] for e in candidate_pairs][:num_i]
    return candidate_items

Đoạn mã này sắp xếp các phim ứng viên dựa trên điểm số của người dùng và chọn ra các phim có điểm số cao nhất. Nó sử dụng trọng số của người dùng để tính điểm cho các phim và chỉ chọn các phim không nằm trong target_seq. Cuối cùng, nó trả về danh sách các phim có điểm số cao nhất.

# Item filtering

In [9]:
def soft_if_items(target_seq, num_i, total_i, item_matrix_sim, item_dict, i_item_id_list, item_id_list):
    candidate_movies_dict = {}  # Tạo một dictionary lưu các phim được chọn

    for movie in target_seq:
        print('Movie in target sequence:', movie)

        # Sắp xếp các item dựa trên độ tương đồng và lấy ra `num_i` item đầu tiên
        sorted_is = sorted(list(enumerate(item_matrix_sim[item_dict[movie]])), key=lambda x: x[-1], reverse=True)[:num_i]

        for is_i, is_v in sorted_is:
            s_item = i_item_id_list[is_i]  # Lấy ID của item tương ứng

            # Nếu item này không nằm trong danh sách target sequence, thêm vào candidate list
            if s_item not in target_seq:
                if s_item not in candidate_movies_dict:
                    candidate_movies_dict[s_item] = 0.0  # Khởi tạo giá trị ban đầu cho item

                candidate_movies_dict[s_item] += is_v  # Cộng dồn độ tương đồng cho item đó

            print(f'Item ID: {item_id_list[is_i]}, Candidate score: {candidate_movies_dict[s_item]}')

    # Sắp xếp các cặp (item, score) theo score từ cao xuống thấp
    candidate_pairs = sorted(candidate_movies_dict.items(), key=lambda x: x[-1], reverse=True)
    print('Sorted candidate pairs:', candidate_pairs)

    # Lấy ra `total_i` item có score cao nhất
    candidate_items = [e[0] for e in candidate_pairs][:total_i]
    print('Candidate items:', candidate_items)

    return candidate_items

Đoạn mã này chọn ra các phim ứng viên dựa trên độ tương đồng với các phim trong target_seq. Nó sử dụng ma trận tương đồng item_matrix_sim để tìm các phim tương tự, sau đó sắp xếp và chọn ra các phim có điểm số cao nhất. Cuối cùng, nó trả về danh sách các phim ứng viên.

# Bước đầu tien

Để tiết kiệm, bước đầu tiên của chúng tôi là xác định các chuỗi người dùng có khả năng cao trong việc đưa ra dự đoán chính xác từ GPT-3.5 dựa trên các ứng viên tương ứng. Sau đó, chúng tôi tiến hành sử dụng API GPT-3.5 để tạo dự đoán cho các chuỗi người dùng đầy hứa hẹn này.

In [14]:
results_data_15 = []
length_limit = args.length_limit  # Giới hạn độ dài
num_u = 12  # Số lượng người dùng cần chọn
total_i = args.num_cand  # Số lượng ứng viên cần chọn
count = 0  # Đếm số lần trúng "HIT"
total = 0  # Tổng số lần kiểm tra
cand_ids = []  # Danh sách ID các ứng viên trúng

# Lặp qua danh sách các ID trong id_list (chỉ lấy 1000 phần tử đầu tiên)
for i in id_list[:1000]:
    elem = data_ml_100k[i]  # Lấy phần tử tương ứng từ data_ml_100k
    seq_list = elem[0].split(' | ')  # Tách chuỗi danh sách phim

    # Lấy danh sách các phim ứng viên dựa trên độ tương đồng của người dùng
    candidate_items = sort_uf_items(seq_list, user_matrix_sim[i], num_u=num_u, num_i=total_i, data_ml_100k=data_ml_100k)

    print(f"{elem[-1]} - {seq_list[-1]}")  # In ra phần tử cuối của elem và phim cuối cùng trong danh sách

    # Kiểm tra xem phim cuối cùng có nằm trong danh sách ứng viên không
    if elem[-1] in candidate_items:
        print('HIT: 1')  # Nếu có, in ra "HIT" và tăng biến đếm
        count += 1
        cand_ids.append(i)  # Lưu ID của phim vào danh sách ứng viên trúng
    else:
        print('HIT: 0')  # Nếu không, in ra "HIT: 0"

    total += 1  # Tăng biến tổng số lần kiểm tra

# In ra tỷ lệ HIT sau khi vòng lặp kết thúc
print(f'count/total: {count}/{total} = {count*1.0/total}')
print('-----------------\n')

Kết quả truyền trực tuyến bị cắt bớt đến 5000 dòng cuối.
Gone with the Wind not in ['Arsenic and Old Lace', 'Nosferatu (Nosferatu, eine Symphonie des Grauens)', 'Hoop Dreams', 'Carmen Miranda: Bananas Is My Business', 'New York Cop', 'Angus', 'Philadelphia', 'The 39 Steps', 'Pinocchio', 'Army of Darkness', 'The Man Without a Face', 'The Browning Version', 'Babyfever', "Schindler's List", 'Terminator 2: Judgment Day', 'The Deer Hunter', 'The Thin Man', 'Young Guns', 'Very Natural Thing, A', 'Speed', 'How to Make an American Quilt', 'Canadian Bacon', 'Wings of Desire', 'Raising Arizona', 'Cape Fear', 'Paths of Glory', 'The Jungle Book', 'My Family', 'Walk in the Sun, A', 'Back to the Future', 'Much Ado About Nothing', 'Kim', 'Cat People', 'Delta of Venus', 'Fluke', 'The Third Man', 'Snow White and the Seven Dwarfs', 'The Old Man and the Sea', 'Mr. Smith Goes to Washington', "National Lampoon's Senior Trip", 'The Wrong Trousers', 'The Last of the Mohicans', 'The Innocents', 'Sabrina', 'Go

Đoạn mã này kiểm tra xem phim cuối cùng trong danh sách của người dùng có nằm trong danh sách các phim ứng viên hay không. Nó tính toán tỷ lệ “HIT” bằng cách đếm số lần phim cuối cùng nằm trong danh sách ứng viên và chia cho tổng số lần kiểm tra. Kết quả được in ra để đánh giá hiệu quả của việc chọn phim ứng viên.

# Phần khác

In [16]:
temp_1 = """
Candidate Set (candidate movies): {}.
The movies I have watched (watched movies): {}.
Step 1: What features are most important to me when selecting movies (Summarize my preferences briefly)?
Answer:
"""

temp_2 = """
Candidate Set (candidate movies): {}.
The movies I have watched (watched movies): {}.
Step 1: What features are most important to me when selecting movies (Summarize my preferences briefly)?
Answer: {}.
Step 2: Selecting the most featured movies from the watched movies according to my preferences (Format: [no. a watched movie.]).
Answer:
"""

temp_3 = """
Candidate Set (candidate movies): {}.
The movies I have watched (watched movies): {}.
Step 1: What features are most important to me when selecting movies (Summarize my preferences briefly)?
Answer: {}.
Step 2: Selecting the most featured movies (at most 5 movies) from the watched movies according to my preferences in descending order (Format: [no. a watched movie.]).
Answer: {}.
Step 3: Can you recommend 10 movies from the Candidate Set similar to the selected movies I've watched (Format: [no. a watched movie - a candidate movie])?.
Answer:
"""

count = 0         # Biến đếm số lần trúng “HIT”.
total = 0         # Tổng số lần kiểm tra.
results_data = [] # Danh sách để lưu trữ kết quả.
for i in cand_ids[:]:                                                                     #[:10] + cand_ids[49:57] + cand_ids[75:81]:
    elem = data_ml_100k[i]
    seq_list = elem[0].split(' | ')[::-1]                                                 #Tách chuỗi danh sách phim và đảo ngược thứ tự.

    candidate_items = sort_uf_items(seq_list, user_matrix_sim[i], num_u=num_u, num_i=total_i, data_ml_100k=data_ml_100k)
    random.shuffle(candidate_items)

    input_1 = temp_1.format(', '.join(candidate_items), ', '.join(seq_list[-length_limit:]))      # Xáo trộn danh sách các phim ứng viên.

    try_nums = 5
    kk_flag = 1
    while try_nums:
        try:
            response = openai.Completion.create(
                      engine="text-davinci-003",
                      prompt=input_1,
                      max_tokens=512,
                      temperature=0,
                      top_p=1,
                      frequency_penalty=0,
                      presence_penalty=0,
                      n = 1,
                  )
            try_nums = 0
            kk_flag = 1
        except Exception as e:
            if 'exceeded your current quota' in str(e):

                # open_ai_keys_index +=1
                openai.api_key = open_ai_keys[open_ai_keys_index]
            time.sleep(1)
            try_nums = try_nums-1
            kk_flag = 0

    if kk_flag == 0:
        time.sleep(5)
        response = openai.Completion.create(
                      engine="text-davinci-003",
                      prompt=input_1,
                      max_tokens=256,
                      temperature=0,
                      top_p=1,
                      frequency_penalty=0,
                      presence_penalty=0,
                      n = 1,
                  )

    predictions_1 = response["choices"][0]['text']


    input_2 = temp_2.format(', '.join(candidate_items), ', '.join(seq_list[-length_limit:]), predictions_1)

    try_nums = 5
    kk_flag = 1
    while try_nums:
        try:
            response = openai.Completion.create(
                      engine="text-davinci-003",
                      prompt=input_2,
                      max_tokens=512,
                      temperature=0,
                      top_p=1,
                      frequency_penalty=0,
                      presence_penalty=0,
                      n = 1,
                  )
            try_nums = 0
            kk_flag = 1
        except Exception as e:
            if 'exceeded your current quota' in str(e):

                # open_ai_keys_index +=1
                openai.api_key = open_ai_keys[open_ai_keys_index]
            time.sleep(1)
            try_nums = try_nums-1
            kk_flag = 0

    if kk_flag == 0:
        time.sleep(5)
        response = openai.Completion.create(
                      engine="text-davinci-003",
                      prompt=input_2,
                      max_tokens=256,
                      temperature=0,
                      top_p=1,
                      frequency_penalty=0,
                      presence_penalty=0,
                      n = 1,
                  )

    predictions_2 = response["choices"][0]['text']


    input_3 = temp_3.format(', '.join(candidate_items), ', '.join(seq_list[-length_limit:]), predictions_1, predictions_2)

    try_nums = 5
    kk_flag = 1
    while try_nums:
        try:
            response = openai.Completion.create(
                      engine="text-davinci-003",
                      prompt=input_3,
                      max_tokens=512,
                      temperature=0,
                      top_p=1,
                      frequency_penalty=0,
                      presence_penalty=0,
                      n = 1,
                  )
            try_nums = 0
            kk_flag = 1
        except Exception as e:
            if 'exceeded your current quota' in str(e):

                # open_ai_keys_index +=1
                openai.api_key = open_ai_keys[open_ai_keys_index]
            time.sleep(1)
            try_nums = try_nums-1
            kk_flag = 0

    if kk_flag == 0:
        time.sleep(5)
        response = openai.Completion.create(
                      engine="text-davinci-003",
                      prompt=input_3,
                      max_tokens=256,
                      temperature=0,
                      top_p=1,
                      frequency_penalty=0,
                      presence_penalty=0,
                      n = 1,
                  )

    predictions = response["choices"][0]['text']


    hit_=0
    if elem[1] in predictions:
        count += 1
        hit_ = 1
    else:
        pass
    total +=1



    #print (f"input_1:{input_1}")
    #print (f"predictions_1:{predictions_1}\n")
    #print (f"input_2:{input_2}")
    #print (f"predictions_2:{predictions_2}\n")
    #print (f"input_3:{input_3}")
    print (f"GT:{elem[1]}")
    print (f"predictions:{predictions}")

    #print (f"GT:{elem[-1]}")
    print (f'PID:{i}; count/total:{count}/{total}={count*1.0/total}\n')
    result_json = {"PID": i,
                   "Input_1": input_1,
                   "Input_2": input_2,
                   "Input_3": input_3,
                   "GT": elem[1],
                   "Predictions_1": predictions_1,
                   "Predictions_2": predictions_2,
                   "Predictions": predictions,
                   'Hit': hit_,
                   'Count': count,
                   'Current_total':total,
                   'Hit@10':count*1.0/total}
    results_data.append(result_json)



file_dir = f"./results_multi_prompting_len{length_limit}_numcand_{total_i}_seed{rseed}.json"
write_json(results_data, file_dir)

User index: 16
User element (first): Grumpier Old Men | Beverly Hills Cop III | City Slickers II: The Legend of Curly's Gold | Michael | Grease 2 | Made in America | Boomerang | Happy Gilmore | Operation Dumbo Drop | Airheads | Hot Shots! Part Deux | The Nutty Professor | Coneheads | Bushwhacked | Tank Girl | Son in Law | Interview with the Vampire | Mary Shelley's Frankenstein | Jaws 2 | Jaws 3-D | Children of the Corn: The Gathering | The Amityville Horror | Wolf | Army of Darkness | Alien 3 | Halloween: The Curse of Michael Myers | Under Siege | Batman Returns | The Empire Strikes Back | Star Trek III: The Search for Spock | Star Trek VI: The Undiscovered Country | Conan the Barbarian | Broken Arrow | Batman | Top Gun | Escape from New York | Jurassic Park | The Three Musketeers | Mission: Impossible | The Rock | Die Hard: With a Vengeance | The Net | Cliffhanger | True Lies | Star Trek: The Motion Picture | Speed | Last Man Standing | Demolition Man | Eraser | Last Action Hero
Grum

APIRemovedInV1: 

You tried to access openai.Completion, but this is no longer supported in openai>=1.0.0 - see the README at https://github.com/openai/openai-python for the API.

You can run `openai migrate` to automatically upgrade your codebase to use the 1.0.0 interface. 

Alternatively, you can pin your installation to the old version, e.g. `pip install openai==0.28`

A detailed migration guide is available here: https://github.com/openai/openai-python/discussions/742


Đoạn mã này thực hiện việc tạo ra các dự đoán từ mô hình GPT-3 dựa trên các phim ứng viên và chuỗi phim của người dùng. Nó thử gọi mô hình GPT-3 nhiều lần nếu gặp lỗi, và nếu thành công, nó lấy kết quả dự đoán từ mô hình. Kết quả này có thể được sử dụng để đánh giá hoặc phân tích thêm.